In [1]:
import pandas, seaborn, scipy, numpy, matplotlib, collections, sklearn, math

%matplotlib inline
from matplotlib import pyplot

# Constants
library_sizes = {
    'WGS': 3002000000,
    'WES': 50160183,
}
mhc_binding_threshold_affinity = 500



%matplotlib inline
%config InlineBackend.figure_format = 'png'

matplotlib.rc("savefig", dpi=800)
#matplotlib.rc("savefig", dpi=72)
#matplotlib.rc('text', usetex=False)
#reload(c)

pandas.set_option('display.max_rows', 500)
pandas.set_option('display.max_columns', 500)

def print_full(x):
    pandas.set_option('display.max_rows', len(x))
    print(x)
    pandas.reset_option('display.max_rows')
    
def bootstrap(values, statistic=numpy.mean, samples=5000):
    values = pandas.Series(values).dropna()
    if len(values) <= 1:
        return (numpy.nan, numpy.nan)
    values = [statistic(sklearn.utils.resample(values)) for i in range(samples)]
    return (numpy.percentile(values, 5), numpy.percentile(values, 95))

def round_to_n(x, n):
    return round(x, -int(math.floor(math.log10(x))) + (n - 1)) 

def mean_with_errorbars(values, decimals=0):
    pattern = "%%0.%df" % decimals
    bars = bootstrap(values)
    if numpy.nan in bars:
        return pattern % numpy.mean(values)
    if decimals == 0:
        bars = (round_to_n(bars[0], 2), round_to_n(bars[1], 2)) 
    return (pattern + " (" + pattern + " - " + pattern + ")") % ((numpy.mean(values),) + bars)


/Users/tim/venvs/analysis-venv-2.7/lib/python2.7/site-packages/matplotlib/__init__.py:872: UserWarning: axes.color_cycle is deprecated and replaced with axes.prop_cycle; please use the latter.
  warnings.warn(self.msg_depr % (key, alt_key))
/Users/tim/venvs/analysis-venv-2.7/lib/python2.7/site-packages/IPython/html.py:14: ShimWarning: The `IPython.html` package has been deprecated. You should import from `notebook` instead. `IPython.html.widgets` has moved to `ipywidgets`.
  "`IPython.html.widgets` has moved to `ipywidgets`.", ShimWarning)


In [2]:
sources = pandas.read_csv("../data/sources.csv", index_col="source_id")
sources = sources.ix[sources.cohort == "AOCS"]


In [15]:
all_signatures = pandas.read_csv("../data/all_signatures.csv", index_col=0)
all_signatures.columns = [c.replace("[", "(").replace("]", ")") for c in all_signatures.columns]
all_signatures.index = [
    x.replace("-", " ").replace(":", " ").replace(".", " ").replace(";", " ").replace("  ", " ")
    for x in all_signatures.index
]
all_signatures

A(C>A)A   A(C>A)C       A(C>A)G   A(C>A)T  \
Signature 1                      0.011098  0.009149  1.490070e-03  0.006234   
Signature 2                      0.000683  0.000619  9.927896e-05  0.000324   
Signature 3                      0.022172  0.017872  2.138340e-03  0.016265   
Signature 4                      0.036500  0.030900  1.830000e-02  0.024300   
Signature 5                      0.014942  0.008961  2.207846e-03  0.009207   
Signature 6                      0.001700  0.002800  5.000000e-04  0.001900   
Signature 7                      0.000400  0.000500  0.000000e+00  0.000400   
Signature 8                      0.036718  0.033246  2.525311e-03  0.033599   
Signature 9                      0.012000  0.006700  5.000000e-04  0.006800   
Signature 10                     0.000700  0.001000  3.000000e-04  0.009200   
Signature 11                     0.000200  0.001000  0.000000e+00  0.000200   
Signature 12                     0.007700  0.004700  1.700000e-03  0.004600   
Signature 13                     0.000335  0.000649  3.814459e-05  0.000847   
Signature 14                     0.000100  0.004200  5.000000e-04  0.029600   
Signature 15                     0.001300  0.004000  0.000000e+00  0.005700   
Signature 16                     0.016100  0.009700  2.200000e-03  0.008800   
Signature 17                     0.001832  0.000342  1.576225e-06  0.003180   
Signature 18                     0.050536  0.010940  2.288073e-03  0.019424   
Signature 19                     0.010700  0.007400  5.000000e-04  0.007400   
Signature 20                     0.001180  0.002212  1.616910e-07  0.003008   
Signature 21                     0.000100  0.000700  0.000000e+00  0.000600   
Signature 22                     0.001504  0.002451  0.000000e+00  0.000922   
Signature 23                     0.000453  0.000367  0.000000e+00  0.000000   
Signature 24                     0.028646  0.020215  2.047900e-02  0.024600   
Signature 25                     0.009897  0.006999  1.448443e-03  0.004967   
Signature 26                     0.002040  0.001487  2.839456e-04  0.000598   
Signature 27                     0.005206  0.004738  7.826979e-04  0.002718   
Signature 28                     0.001397  0.000917  0.000000e+00  0.000513   
Signature 29                     0.069982  0.055152  1.784698e-02  0.026805   
Signature 30                     0.000000  0.000000  1.967300e-03  0.000000   
Cisplatin Gallus gallus          0.005651  0.103384  4.697643e-04  0.023226   
Cyclophosphamide Gallus gallus   0.005414  0.006806  1.082130e-03  0.008658   
Etoposide Gallus gallus          0.015258  0.010906  4.453197e-03  0.007189   
Cisplatin C Elegans wildtype     0.007270  0.008788  1.982188e-03  0.010452   
Cisplatin C Elegans fan 1        0.012589  0.009288  2.188741e-03  0.007675   
Cisplatin C Elegans fcd 2        0.007211  0.014533  1.994404e-03  0.007051   
Cisplatin C Elegans lig 4        0.013727  0.014442  2.041499e-03  0.011421   
Cisplatin C Elegans lig 4 fcd 2  0.010548  0.007777  1.745091e-03  0.009839   
Cisplatin C Elegans mus 81       0.008637  0.010169  2.293798e-03  0.007808   
Cisplatin C Elegans polq 1       0.017243  0.014713  4.673353e-03  0.007463   
Cisplatin C Elegans slx 1        0.012151  0.014158  2.018952e-03  0.007131   
Cisplatin C Elegans xpf 1        0.004080  0.009058  1.100558e-03  0.014444   

                                  A(C>G)A   A(C>G)C   A(C>G)G   A(C>G)T  \
Signature 1                      0.001801  0.002581  0.000593  0.002964   
Signature 2                      0.000263  0.000270  0.000219  0.000611   
Signature 3                      0.024003  0.012160  0.005275  0.023278   
Signature 4                      0.009700  0.005400  0.003100  0.005400   
Signature 5                      0.011671  0.007292  0.002304  0.011696   
Signature 6                      0.001300  0.001200  0.000000  0.001800   
Signature 7                      0.000000  0.000000  0.000000  0.000100   
Signature 8                      0.0

In [16]:
deconvolution_df = pandas.read_csv("../data/deconstructsigs_output.cleaned.csv",
                                   index_col=["source_id", "kind"])
for col in deconvolution_df.columns:
    if col.endswith(".1"):
        deconvolution_df[col[:-2]] = deconvolution_df[col]
        del deconvolution_df[col]
deconvolution_df

Signature 1  Signature 2  Signature 3  Signature 4  \
source_id            kind                                                       
AOCS-166-1/SP102133  all      0.000000     0.000000     0.000000     0.000000   
AOCS-092-13/SP101630 new      0.000000     0.000000     0.133002     0.000000   
AOCS-119-13/SP101732 all      0.000000     0.000000     0.217817     0.000000   
AOCS-117-13/SP101724 all      0.000000     0.000000     0.243353     0.000000   
AOCS-135-13/SP101855 all      0.000000     0.000000     0.272220     0.000000   
AOCS-135-14/SP101860 all      0.000000     0.000000     0.276793     0.000000   
AOCS-150-13/SP102010 all      0.000000     0.000000     0.293942     0.000000   
AOCS-004-1/SP101519  all      0.000000     0.000000     0.325053     0.000000   
AOCS-088-1/SP101610  all      0.000000     0.000000     0.331926     0.000000   
AOCS-034-13/SP101524 new      0.000000     0.000000     0.340932     0.000000   
AOCS-092-13/SP101630 all      0.000000     0.000000     0.361248     0.000000   
AOCS-125-1/SP101775  all      0.000000     0.000000     0.362537     0.000000   
AOCS-088-13/SP101612 all      0.000000     0.000000     0.367817     0.000000   
AOCS-086-13/SP101606 new      0.000000     0.000000     0.368232     0.000000   
AOCS-095-13/SP101650 all      0.000000     0.000000     0.382850     0.000000   
AOCS-107-1/SP101674  all      0.000000     0.000000     0.385446     0.000000   
AOCS-088-13/SP101612 new      0.000000     0.000000     0.388024     0.000000   
AOCS-128-1/SP101795  all      0.000000     0.000000     0.389620     0.000000   
AOCS-095-13/SP101650 new      0.000000     0.000000     0.394736     0.000000   
AOCS-122-1/SP101748  all      0.000000     0.000000     0.398963     0.000000   
AOCS-093-13/SP101638 new      0.000000     0.000000     0.403519     0.000000   
AOCS-148-1/SP101990  all      0.000000     0.000000     0.410174     0.000000   
AOCS-064-1/SP101552  all      0.000000     0.000000     0.425251     0.000000   
AOCS-155-13/SP102045 all      0.000000     0.000000     0.426403     0.000000   
AOCS-150-14/SP102015 all      0.000000     0.000000     0.426651     0.000000   
AOCS-158-1/SP102064  all      0.000000     0.000000     0.427354     0.000000   
AOCS-131-1/SP101815  all      0.000000     0.000000     0.429348     0.000000   
AOCS-167-4/SP102151  all      0.000000     0.000000     0.432883     0.000000   
AOCS-138-13/SP101881 all      0.000000     0.000000     0.433607     0.000000   
AOCS-146-1/SP101971  all      0.000000     0.000000     0.436339     0.000000   
AOCS-167-13/SP102143 all      0.000000     0.000000     0.447755     0.000000   
AOCS-139-17/SP101901 new      0.000000     0.000000     0.451009     0.000000   
AOCS-137-13/SP101871 all      0.000000     0.000000     0.459749     0.000000   
AOCS-064-13/SP101554 all      0.000000     0.000000     0.463063     0.000000   
AOCS-034-13/SP101524 all      0.000000     0.000000     0.463620     0.000000   
AOCS-139-4/SP101906  new      0.000000     0.000000     0.465730     0.000000   
AOCS-139-16/SP101896 new      0.000000     0.000000     0.470709     0.000000   
AOCS-064-13/SP101554 new      0.000000     0.000000     0.486441     0.000000   
AOCS-139-16/SP101896 all      0.000000     0.000000     0.488249     0.000000   
AOCS-139-4/SP101906  all      0.000000     0.000000     0.489765     0.000000   
AOCS-091-13/SP101624 new      0.000000     0.000000     0.491686     0.000000   
AOCS-171-1/SP102187  all      0.000000     0.000000     0.499955     0.000000   
AOCS-091-13/SP101624 all      0.000000     0.000000     0.504162     0.000000   
AOCS-091-1/SP101622  all      0.000000     0.000000     0.509180     0.000000   
AOCS-086-13/SP101606 all      0.000000     0.000000     0.515186     0.000000   
AOCS-094-2/SP106641  new      0.000000     0.000000     0.516900     0.000000   
AOCS-137-13/SP101871 new      0.000000     0.000000     0.543342     0.000000   
AOCS-120-13/SP101740 all      0.000000     0.000000     0.

In [17]:
full_signatures = deconvolution_df.ix[deconvolution_df.kind == "all"].copy()
del full_signatures["treated"]
del full_signatures["kind"]
del full_signatures["source_id"]


full_signatures.index = full_signatures.index.droplevel(1)
untreated_full_signatures = full_signatures.ix[[s for s in sources.ix[~sources.treated].index ]].dropna()
untreated_full_signatures

Signature 1  Signature 2  Signature 3  Signature 4  \
source_id                                                                  
AOCS-001-1/SP101515      0.078425     0.000000     0.427109     0.000000   
AOCS-002-1/SP101517      0.210230     0.000000     0.000000     0.000000   
AOCS-004-1/SP101519      0.000000     0.000000     0.325053     0.000000   
AOCS-005-1/SP101521      0.137165     0.000000     0.182306     0.000000   
AOCS-034-1/SP101523      0.090249     0.000000     0.618937     0.000000   
AOCS-055-1/SP101526      0.099439     0.071493     0.289350     0.000000   
AOCS-056-1/SP101528      0.106517     0.000000     0.489868     0.000000   
AOCS-057-1/SP101530      0.070367     0.000000     0.364300     0.000000   
AOCS-058-1/SP101532      0.091644     0.000000     0.392199     0.063141   
AOCS-059-1/SP101536      0.301725     0.000000     0.104164     0.000000   
AOCS-060-1/SP101540      0.372829     0.000000     0.096577     0.000000   
AOCS-061-1/SP101544      0.188741     0.000000     0.174318     0.000000   
AOCS-063-1/SP101548      0.100592     0.000000     0.333666     0.000000   
AOCS-064-1/SP101552      0.000000     0.000000     0.425251     0.000000   
AOCS-065-1/SP101558      0.072363     0.000000     0.428038     0.000000   
AOCS-075-1/SP101564      0.173227     0.000000     0.282956     0.000000   
AOCS-076-1/SP101568      0.179174     0.000000     0.261555     0.000000   
AOCS-078-1/SP101576      0.145863     0.000000     0.427427     0.000000   
AOCS-079-1/SP101580      0.107297     0.000000     0.287521     0.000000   
AOCS-080-1/SP101584      0.188922     0.000000     0.302216     0.000000   
AOCS-081-1/SP101588      0.230859     0.000000     0.357072     0.000000   
AOCS-083-1/SP101592      0.156830     0.000000     0.273711     0.000000   
AOCS-084-1/SP101596      0.161559     0.000000     0.181019     0.000000   
AOCS-085-1/SP101600      0.137891     0.000000     0.000000     0.000000   
AOCS-086-1/SP101604      0.107705     0.000000     0.605404     0.000000   
AOCS-088-1/SP101610      0.000000     0.000000     0.331926     0.000000   
AOCS-090-1/SP101616      0.104742     0.000000     0.513598     0.000000   
AOCS-091-1/SP101622      0.000000     0.000000     0.509180     0.000000   
AOCS-092-1/SP101628      0.142299     0.000000     0.414787     0.000000   
AOCS-093-1/SP101634      0.068029     0.000000     0.648383     0.000000   
AOCS-093-12/SP101636     0.071473     0.000000     0.654165     0.000000   
AOCS-094-1/SP101642      0.000000     0.000000     0.567906     0.000000   
AOCS-095-1/SP101648      0.072325     0.000000     0.443461     0.000000   
AOCS-096-1/SP101654      0.090235     0.000000     0.110565     0.000000   
AOCS-097-1/SP101658      0.297378     0.000000     0.128924     0.000000   
AOCS-104-1/SP101662      0.069282     0.000000     0.404953     0.000000   
AOCS-105-1/SP101666      0.088620     0.000000     0.405975     0.000000   
AOCS-107-1/SP101674      0.000000     0.000000     0.385446     0.000000   
AOCS-108-1/SP101678      0.071535     0.000000     0.496188     0.000000   
AOCS-109-1/SP101682      0.292491     0.000000     0.000000     0.000000   
AOCS-111-1/SP101686      0.297177     0.000000     0.221952     0.000000   
AOCS-112-1/SP101690      0.129531     0.000000     0.356287     0.000000   
AOCS-113-1/SP101694      0.172822     0.000000     0.206601     0.000000   
AOCS-114-1/SP101700      0.087789     0.000000     0.372706     0.000000   
AOCS-115-1/SP101708      0.173976     0.000000     0.221258     0.000000   
AOCS-116-1/SP101716      0.125318     0.000000     0.295477     0.000000   
AOCS-122-1/SP101748      0.000000     0.000000     0.398963     0.000000   
AOCS-123-1/SP101756      0.246706     0.000000     0.118139     0.000000   
AOCS-124-1/SP101765      0.261362     0.000000     0.126405     0.000000   
AOCS-125-1/SP101775      0.000000     0.000000     0.362537     0.000000   
AOCS-126-1/SP101785      0.067636     0.000000     0.490194     0.0000

In [18]:
new_signatures = deconvolution_df.ix[deconvolution_df.kind == "new"]
del new_signatures["treated"]
del new_signatures["kind"]
del new_signatures["source_id"]

new_signatures.index = new_signatures.index.droplevel(1)
new_signatures

Signature 1  Signature 2  Signature 3  Signature 4  \
source_id                                                                  
AOCS-092-13/SP101630            0            0     0.133002            0   
AOCS-034-13/SP101524            0            0     0.340932            0   
AOCS-086-13/SP101606            0            0     0.368232            0   
AOCS-088-13/SP101612            0            0     0.388024            0   
AOCS-095-13/SP101650            0            0     0.394736            0   
AOCS-093-13/SP101638            0            0     0.403519            0   
AOCS-139-17/SP101901            0            0     0.451009            0   
AOCS-139-4/SP101906             0            0     0.465730            0   
AOCS-139-16/SP101896            0            0     0.470709            0   
AOCS-064-13/SP101554            0            0     0.486441            0   
AOCS-091-13/SP101624            0            0     0.491686            0   
AOCS-094-2/SP106641             0            0     0.516900            0   
AOCS-137-13/SP101871            0            0     0.543342            0   
AOCS-065-13/SP101560            0            0     0.562300            0   

                      Signature 5  Signature 6  Signature 8  Signature 9  \
source_id                                                                  
AOCS-092-13/SP101630            0            0     0.000000     0.000000   
AOCS-034-13/SP101524            0            0     0.102470     0.000000   
AOCS-086-13/SP101606            0            0     0.000000     0.000000   
AOCS-088-13/SP101612            0            0     0.314133     0.000000   
AOCS-095-13/SP101650            0            0     0.000000     0.000000   
AOCS-093-13/SP101638            0            0     0.000000     0.000000   
AOCS-139-17/SP101901            0            0     0.179087     0.000000   
AOCS-139-4/SP101906             0            0     0.181527     0.000000   
AOCS-139-16/SP101896            0            0     0.170599     0.000000   
AOCS-064-13/SP101554            0            0     0.098520     0.000000   
AOCS-091-13/SP101624            0            0     0.085732     0.000000   
AOCS-094-2/SP106641             0            0     0.163105     0.000000   
AOCS-137-13/SP101871            0            0     0.000000     0.000000   
AOCS-065-13/SP101560            0            0     0.079246     0.090869   

                      Signature 10  Signature 12  Signature 13  Signature 14  \
source_id                                                                      
AOCS-092-13/SP101630             0      0.000000      0.000000             0   
AOCS-034-13/SP101524             0      0.000000      0.177889             0   
AOCS-086-13/SP101606             0      0.000000      0.000000             0   
AOCS-088-13/SP101612             0      0.000000      0.079716             0   
AOCS-095-13/SP101650             0      0.000000      0.000000             0   
AOCS-093-13/SP101638             0      0.000000      0.000000             0   
AOCS-139-17/SP101901             0      0.000000      0.000000             0   
AOCS-139-4/SP101906              0      0.000000      0.000000             0   
AOCS-139-16/SP101896             0      0.000000      0.000000             0   
AOCS-064-13/SP101554             0      0.000000      0.000000             0   
AOCS-091-13/SP101624             0      0.000000      0.000000             0   
AOCS-094-2/SP106641              0      0.078054      0.061532             0   
AOCS-137-13/SP101871             0      0.000000      0.000000             0   
AOCS-065-13/SP101560             0      0.000000      0.000000             0   

                      Signature 16  Signature 18  Signature 19  Signature 22  \
source_id                                                                      
AOCS-092-13/SP101630      0.000000             0      0.094217      0.120342   
AOCS-034-13/SP101524      0.000000             0      0.000000     

In [19]:
mutations = pandas.read_csv("../data/mutations.csv.bz2")
mutations["indel"] = mutations.ref.str.len() != mutations.alt.str.len()


In [20]:
primary_mutations_with_signatures = mutations.ix[
    mutations.snv & mutations.source_id.isin(untreated_full_signatures.index)]
new_mutations_with_signatures = mutations.ix[
    mutations.snv & mutations.source_id.isin(new_signatures.index) & mutations.unique_to_treated
]

def add_signature_columns(mutations_df, signature_participations, all_signatures):
    mutations_df = mutations_df.copy().reset_index()
    extra_columns = []
    for (i, row) in mutations_df.iterrows():
        unnormalized = numpy.array([
            all_signatures.ix[signature][row.context_mutation_3p5p] * participation
            for (signature, participation) in signature_participations.ix[row.source_id].iteritems()
        ])
        if numpy.isnan(unnormalized).any():
            print(i, row, unnormalized, signature, row.context_mutation_3p5, participation)
            raise ValueError()
        normalized = unnormalized / unnormalized.sum()
        extra_columns.append(normalized)
    new_df = pandas.DataFrame(extra_columns, columns=signature_participations.columns)
    for col in new_df.columns:
        mutations_df[col] = new_df[col]
    return mutations_df


primary_mutations_with_signatures = add_signature_columns(
    primary_mutations_with_signatures, untreated_full_signatures, all_signatures)
primary_mutations_with_signatures

new_mutations_with_signatures = add_signature_columns(
    new_mutations_with_signatures, new_signatures, all_signatures)
new_mutations_with_signatures
            

index             source_id     donor  called  genome contig  \
0             0   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     18   
1             1  AOCS-139-16/SP101896  AOCS-139       0  GRCh37     18   
2             2   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
3             3  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
4             4   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     18   
5             5  AOCS-139-16/SP101896  AOCS-139       0  GRCh37     18   
6             6   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     18   
7             7  AOCS-139-16/SP101896  AOCS-139       0  GRCh37     18   
8             8  AOCS-139-16/SP101896  AOCS-139       1  GRCh37     18   
9             9   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     18   
10           10   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
11           11  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
12           12   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
13           13  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
14           23  AOCS-139-16/SP101896  AOCS-139       1  GRCh37     18   
15           24   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     18   
16           25   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
17           26  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
18           27  AOCS-139-17/SP101901  AOCS-139       1  GRCh37     18   
19           28  AOCS-139-16/SP101896  AOCS-139       1  GRCh37     18   
20           29   AOCS-139-4/SP101906  AOCS-139       0  GRCh37     18   
21           34   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
22           35  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
23           36  AOCS-139-16/SP101896  AOCS-139       1  GRCh37      6   
24           37   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
25           38  AOCS-139-17/SP101901  AOCS-139       1  GRCh37     18   
26           45  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
27           46   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
28           47  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
29           48  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
30           49  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
31           50   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
32           51  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
33           53  AOCS-139-16/SP101896  AOCS-139       1  GRCh37     19   
34           54   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     19   
35           55  AOCS-139-16/SP101896  AOCS-139       1  GRCh37      6   
36           56   AOCS-139-4/SP101906  AOCS-139       0  GRCh37      6   
37           57  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
38           71  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
39           72  AOCS-139-16/SP101896  AOCS-139       1  GRCh37      6   
40           73   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
41           82  AOCS-139-16/SP101896  AOCS-139       1  GRCh37     19   
42           83   AOCS-139-4/SP101906  AOCS-139       1  GRCh37     19   
43           85  AOCS-139-16/SP101896  AOCS-139       1  GRCh37      6   
44           86   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
45           89  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
46          102  AOCS-139-17/SP101901  AOCS-139       1  GRCh37     19   
47          105  AOCS-139-17/SP101901  AOCS-139       1  GRCh37     19   
48          107   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
49          108  AOCS-139-16/SP101896  AOCS-139       0  GRCh37      6   
50          109  AOCS-139-17/SP101901  AOCS-139       1  GRCh37      6   
51          110  AOCS-139-16/SP101896  AOCS-139       1  GRCh37      6   
52          111   AOCS-139-4/SP101906  AOCS-139       1  GRCh37      6   
53          11

In [21]:
mutations_with_signatures = pandas.concat([
        primary_mutations_with_signatures.ix[sources.index[~sources.treated]],
        new_mutations_with_signatures,
])
print(mutations_with_signatures.shape)
mutations_with_signatures

(106250, 71)


index             source_id     donor  called  genome  \
source_id                                                                       
AOCS-001-1/SP101515       NaN                   NaN       NaN     NaN     NaN   
AOCS-002-1/SP101517       NaN                   NaN       NaN     NaN     NaN   
AOCS-004-1/SP101519       NaN                   NaN       NaN     NaN     NaN   
AOCS-005-1/SP101521       NaN                   NaN       NaN     NaN     NaN   
AOCS-034-1/SP101523       NaN                   NaN       NaN     NaN     NaN   
AOCS-055-1/SP101526       NaN                   NaN       NaN     NaN     NaN   
AOCS-056-1/SP101528       NaN                   NaN       NaN     NaN     NaN   
AOCS-057-1/SP101530       NaN                   NaN       NaN     NaN     NaN   
AOCS-058-1/SP101532       NaN                   NaN       NaN     NaN     NaN   
AOCS-059-1/SP101536       NaN                   NaN       NaN     NaN     NaN   
AOCS-060-1/SP101540       NaN                   NaN       NaN     NaN     NaN   
AOCS-061-1/SP101544       NaN                   NaN       NaN     NaN     NaN   
AOCS-063-1/SP101548       NaN                   NaN       NaN     NaN     NaN   
AOCS-064-1/SP101552       NaN                   NaN       NaN     NaN     NaN   
AOCS-065-1/SP101558       NaN                   NaN       NaN     NaN     NaN   
AOCS-075-1/SP101564       NaN                   NaN       NaN     NaN     NaN   
AOCS-076-1/SP101568       NaN                   NaN       NaN     NaN     NaN   
AOCS-078-1/SP101576       NaN                   NaN       NaN     NaN     NaN   
AOCS-079-1/SP101580       NaN                   NaN       NaN     NaN     NaN   
AOCS-080-1/SP101584       NaN                   NaN       NaN     NaN     NaN   
AOCS-081-1/SP101588       NaN                   NaN       NaN     NaN     NaN   
AOCS-083-1/SP101592       NaN                   NaN       NaN     NaN     NaN   
AOCS-084-1/SP101596       NaN                   NaN       NaN     NaN     NaN   
AOCS-085-1/SP101600       NaN                   NaN       NaN     NaN     NaN   
AOCS-086-1/SP101604       NaN                   NaN       NaN     NaN     NaN   
AOCS-088-1/SP101610       NaN                   NaN       NaN     NaN     NaN   
AOCS-090-1/SP101616       NaN                   NaN       NaN     NaN     NaN   
AOCS-091-1/SP101622       NaN                   NaN       NaN     NaN     NaN   
AOCS-092-1/SP101628       NaN                   NaN       NaN     NaN     NaN   
AOCS-093-1/SP101634       NaN                   NaN       NaN     NaN     NaN   
AOCS-093-12/SP101636      NaN                   NaN       NaN     NaN     NaN   
AOCS-094-1/SP101642       NaN                   NaN       NaN     NaN     NaN   
AOCS-095-1/SP101648       NaN                   NaN       NaN     NaN     NaN   
AOCS-096-1/SP101654       NaN                   NaN       NaN     NaN     NaN   
AOCS-097-1/SP101658       NaN                   NaN       NaN     NaN     NaN   
AOCS-104-1/SP101662       NaN                   NaN       NaN     NaN     NaN   
AOCS-105-1/SP101666       NaN                   NaN       NaN     NaN     NaN   
AOCS-107-1/SP101674       NaN                   NaN       NaN     NaN     NaN   
AOCS-108-1/SP101678       NaN                   NaN       NaN     NaN     NaN   
AOCS-109-1/SP101682       NaN                   NaN       NaN     NaN     NaN   
AOCS-111-1/SP101686       NaN                   NaN       NaN     NaN     NaN   
AOCS-112-1/SP101690       NaN                   NaN       NaN     NaN     NaN   
AOCS-113-1/SP101694       NaN                   NaN       NaN     NaN     NaN   
AOCS-114-1/SP101700       NaN                   NaN       NaN     NaN     NaN   
AOCS-115-1/SP101708       NaN                   NaN       NaN     NaN     NaN   
AOCS-116-1/SP101716       NaN                   NaN       NaN     NaN     NaN   
AOCS-122-1/SP101748       NaN                   NaN       NaN     NaN     NaN   
AOCS-123-1/SP101756       NaN                   NaN    

In [22]:
muts_confident = mutations.ix[
    (mutations.called == 1) | (mutations.dna_alt_reads > 10)
]
aocs_muts = mutations.ix[mutations.donor.str.startswith("AOCS")]
aocs_muts_confident = muts_confident.ix[muts_confident.donor.str.startswith("AOCS")]
aocs_muts_confident_coding = aocs_muts_confident.ix[aocs_muts_confident.effect.str.startswith("p.")]
aocs_muts_confident_coding_expressed = aocs_muts_confident_coding.ix[aocs_muts_confident_coding.rna_alt_reads > 2]

non_exon_effects = [
    "intergenic",
    "intragenic",
    "intronic",
    "non-coding-transcript",
    "incomplete",
    "splice-acceptor",
    "splice-donor",
    "intronic-splice-site",
    "exonic-splice-site",
    "3' UTR",
    "5' UTR",
]

aocs_muts_confident_exon = aocs_muts_confident.ix[~ aocs_muts_confident.effect.isin(non_exon_effects)]
aocs_muts_exon = aocs_muts.ix[~ aocs_muts.effect.isin(non_exon_effects)]

[x for x in aocs_muts_confident_exon.effect.unique().tolist() if not x.startswith("p.")]

['silent']

In [ ]:
display_signatures = ["Signature 1", "Signature 3", "Signature 8"]

sources_with_signature_counts = sources.copy()
for source_id, grouped in mutations_with_signatures.groupby("source_id"):
    if sources.ix[source_id].treated:
        sub_all_muts = mutations.ix[(mutations.source_id == source_id) & mutations.unique_to_treated]
        sub_exon_muts = aocs_muts_exon.ix[(mutations.source_id == source_id) & mutations.unique_to_treated]
    else:
        sub_all_muts = mutations.ix[(mutations.source_id == source_id)]
        sub_exon_muts = aocs_muts_exon.ix[(mutations.source_id == source_id)]
        
    num_mutations = float(sub_all_muts.shape[0])
    num_exon_mutations = float(sub_exon_muts.shape[0])
    num_neoantigens = float(sub_all_muts.num_binders.sum())
    
    snv_mutations_accounted_for = 0.0
    snv_neoantigens_accounted_for = 0.0
    for sig in display_signatures:
        snv_mutations_accounted_for += grouped[sig].sum()
        snv_neoantigens_accounted_for += numpy.dot(grouped[sig], grouped.num_binders)
        
        sources_with_signature_counts.loc[source_id, "%s mutations" % sig] = grouped[sig].sum() / num_mutations
        sources_with_signature_counts.loc[source_id, "%s neoantigens" % sig] = (
            numpy.dot(grouped[sig], grouped.num_binders)) / num_neoantigens
    
    snv_mutations = sub_all_muts.snv.sum()
    snv_neoantigens = sub_all_muts.ix[sub_all_muts.snv].num_binders.sum()
    
    sources_with_signature_counts.loc[source_id, "other snv mutations"] = (
        snv_mutations - snv_mutations_accounted_for) / num_mutations
    sources_with_signature_counts.loc[source_id, "other snv neoantigens"] = (
        snv_neoantigens - snv_neoantigens_accounted_for) / num_neoantigens

    sources_with_signature_counts.loc[source_id, "snv mutations"] = snv_mutations
    sources_with_signature_counts.loc[source_id, "snv neoantigens"] = snv_neoantigens
    
    sources_with_signature_counts.loc[source_id, "mnv mutations"] = (
        (~ sub_all_muts.indel) & (~ sub_all_muts.snv)).sum() / num_mutations
    sources_with_signature_counts.loc[source_id, "mnv neoantigens"] = (
        sub_all_muts.ix[(~ sub_all_muts.indel) & (~ sub_all_muts.snv)].num_binders.sum()) / num_neoantigens
    
    sources_with_signature_counts.loc[source_id, "indel mutations"] = (
        (sub_all_muts.indel).sum()) / num_exon_mutations
    sources_with_signature_counts.loc[source_id, "indel neoantigens"] = (
        sub_all_muts.ix[sub_all_muts.indel].num_binders.sum()) / num_neoantigens
    
sources_with_signature_counts[sources_with_signature_counts.paired]
    